In [10]:
import sqlite3
import pandas as pd

db_path = 'D:\\code\\uom_explore\\database\\voc_lab_2.db'

conn = sqlite3.connect(db_path)

# Define the specific conditions
experiment_batch = 'exp_efficiency_test_async_1'
experiment_id = '20240726121620s1c0r0'

# Write the query to select specific columns based on conditions
query = f"""
SELECT channel_id, heater_setting, timestamp, sensor_value
FROM ExperimentData
WHERE experiment_batch = ?
AND experiment_id = ?
"""

# Execute the query and load the data into a DataFrame
df = pd.read_sql_query(query, conn, params=(experiment_batch, experiment_id))

# Close the database connection
conn.close()

grouped = df.groupby('heater_setting', as_index=False, group_keys=False)

def normalize_timstamp(group):
    group['timestamp'] = group['timestamp'] - group['timestamp'].iloc[0]
    return group

df_ts = grouped.apply(normalize_timstamp).reset_index(drop=True)
grouped_ts = df_ts.groupby('heater_setting')

print (grouped_ts.head(5))

     channel_id  heater_setting  timestamp  sensor_value
0             0             140          0       11734.0
1             0             150          0       11734.0
2             0             152          0       11734.0
3             0             155          0       11734.0
4             0             157          0       11734.0
..          ...             ...        ...           ...
200           0             220        226        9501.0
201           0             222        226        9649.0
202           0             225        225        9799.0
203           0             227        225        9799.0
204           0             230        225        9955.0

[205 rows x 4 columns]


C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\1678721383.py:32: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df_ts = grouped.apply(normalize_timstamp).reset_index(drop=True)


In [11]:
# use plotly to explore the data interactively
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
from scipy.signal import butter, filtfilt


# Filter requirements.
order = 6
fs = 30.0  # sample rate, Hz
cutoff = 3.66  # desired cutoff frequency of the filter, Hz
window_size = 30
group_channel = 'sensor_value'

# apply low pass filter to each group
def apply_filter(group, order, fs, cutoff, group_channel, window_size):
    # Get the filter coefficients
    b, a = butter(order, cutoff / (fs / 2), btype='low', analog=False)
    group['ADC_filtered'] = filtfilt(b, a, group[group_channel])
    group['ADC_filtered'] = group['ADC_filtered'].rolling(window_size, center=True).median()
    return group


# Apply the filter to each group
df_normalized = grouped_ts.apply(apply_filter, order=order, fs=fs, cutoff=cutoff, group_channel=group_channel, window_size=window_size).reset_index(drop=True)
input_voltage = 3.3
RL_2 = 10000 # 10kOhm

# convert to resistance where R_laod is R2 = 10kOhm input_voltage = 3.3V and 1_bit = 0.125mV (3.3V/2^14)
df_normalized['Vo'] = df_normalized['ADC_filtered']*0.000125
df_normalized['Resistance'] = (RL_2/df_normalized['Vo'])*((input_voltage/df_normalized['Vo'])-1)


# Define the figure without subplots as we are plotting only one channel
fig = go.Figure()

# The channel to plot
channel = 'Resistance' 
# 'ADC_filtered'

# Plot the channel
for setting in df_normalized['heater_setting'].unique():
    # Filter the DataFrame for each setting
    df_filtered = df_normalized[df_normalized['heater_setting'] == setting]
    fig.add_trace(
        go.Scatter(
            x=df_filtered['timestamp'],
            y=df_filtered[channel],
            mode='lines',
            name=f'Setting {setting}',
            # Optionally, you can uncomment and adjust the line color settings if needed
            # line=dict(color=colors[setting % len(colors)])  # Loop through colors cyclically
        )
    )

# Set titles and axes labels
fig.update_xaxes(title_text='Timestamp')
fig.update_yaxes(title_text=channel)
fig.update_layout(height=500, width=800, title_text=f'{channel} vs. Timestamp', showlegend=True)

# Display figure
fig.show()

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\3899351365.py:25: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df_normalized = grouped_ts.apply(apply_filter, order=order, fs=fs, cutoff=cutoff, group_channel=group_channel, window_size=window_size).reset_index(drop=True)


In [12]:
# show the number of unique heater_settings
print (df_normalized['heater_setting'].unique())

[140 150 152 155 157 160 162 165 167 170 172 175 177 180 182 185 187 190
 192 195 197 200 202 205 210 212 215 217 220 222 225 227 230 232 235 237
 240 242 245 247 250]


# Transform each experiment into a single feature 

|feature 1|feature 2|feature 3...| ground truth (class)
- each feature is the ratio of a temperature
- each row is a dataset
- each file contain 41 settings 

In [13]:
# from the database retrieve the all experiment_id, heater_setting, sensor_value, channel_id

db_path = 'D:\\code\\uom_explore\\database\\voc_lab_2.db'

conn = sqlite3.connect(db_path)

# Write the query to select specific columns based on conditions
query = f"""
SELECT experiment_id, heater_setting, timestamp, sensor_value, channel_id
FROM ExperimentData
"""

# Execute the query and load the data into a DataFrame
df = pd.read_sql_query(query, conn)
df.tail()

experiment_id  heater_setting  timestamp  sensor_value  \
8280040  20240729115332s1c4r19             227    4628609       26157.0   
8280041  20240729115332s1c4r19             230    4628620       26156.0   
8280042  20240729115332s1c4r19             232    4628631       26158.0   
8280043  20240729115332s1c4r19             235    4628641       26160.0   
8280044  20240729115332s1c4r19             237    4628652       26156.0   

         channel_id  
8280040           4  
8280041           4  
8280042           4  
8280043           4  
8280044           4

In [14]:

# group df by experiment_id and heater_setting
grouped = df.groupby(['experiment_id', 'heater_setting'], as_index=False, group_keys=False)

# normalise
def normalize_timstamp(group):
    group['timestamp'] = group['timestamp'] - group['timestamp'].iloc[0]
    return group

df_ts = grouped.apply(normalize_timstamp).reset_index(drop=True)
grouped_ts = df_ts.groupby(['experiment_id','heater_setting'], as_index=False, group_keys=False)

# Filter requirements.
order = 6
fs = 30.0  # sample rate, Hz
cutoff = 3.66  # desired cutoff frequency of the filter, Hz
window_size = 30
target_channel = 'sensor_value'

# apply low pass filter to each group
def apply_filter(group, order, fs, cutoff, target_channel, window_size):
  # Get the filter coefficients
  # b, a = butter(order, cutoff / (fs / 2), btype='low', analog=False)
  # group['filtered'] = filtfilt(b, a, group[group_channel])
  group['filtered'] = group[target_channel].rolling(window_size, center=False).median()
  return group


# within each experiment_id group, apply the filter to each heater_setting group
# df_filtered = grouped_ts.apply(apply_filter, order=order, fs=fs, cutoff=cutoff, target_channel=group_channel, window_size=window_size).reset_index(drop=True)

filtered_data = []
for name, group in grouped_ts:
  filtered_group = group.copy()  # Avoid modifying original data
  filtered_group['filtered'] = group['sensor_value'].rolling(window_size, center=False).mean()
  filtered_data.append(filtered_group)

df_filtered = pd.concat(filtered_data, ignore_index=True)


# convert to resistance where R_laod is R2 = 10kOhm input_voltage = 3.3V and 1_bit = 0.125mV (3.3V/2^14)
input_voltage = 3.3
RL_2 = 10000 # 10kOhm

# convert to resistance where R_laod is R2 = 10kOhm input_voltage = 3.3V and 1_bit = 0.125mV (3.3V/2^14)
df_normalized['Vo'] = df_filtered['sensor_value']*0.000125
df_normalized['Resistance'] = (RL_2/df_normalized['Vo'])*((input_voltage/df_normalized['Vo'])-1)


C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\3902438630.py:9: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



## Retrieve a specific group

In [15]:
import plotly.express as px

experiment_id_value = "20240726121620s1c0r0"	# Example value for experiment_id
heater_setting_value = 140  # Example value for heater setting

# Use a tuple to get the specific group
group = grouped_ts.get_group((experiment_id_value, heater_setting_value))

# Now you can plot this group
fig = px.line(group, x='timestamp', y='sensor_value', title=f'Experiment {experiment_id_value} - Heater Setting {heater_setting_value}')
fig.show()

## Retrieve with index

In [16]:
# plot one specific group with plotly
import plotly.express as px

# Group by 'experiment_id' and 'heater_setting'
grouped_ts = df_ts.groupby(['experiment_id', 'heater_setting'], as_index=False, group_keys=False)

# Convert the groups to a list
groups = list(grouped_ts.groups.keys())

# Use the index to get the specific group
index = 0  # Replace with the desired index
experiment_id_value, heater_setting_value = groups[index]

# Fetch the specific group
group = grouped_ts.get_group((experiment_id_value, heater_setting_value))

# Now you can plot this group
fig = px.line(group, x='timestamp', y='sensor_value', title=f'Experiment {experiment_id_value} - Heater Setting {heater_setting_value}')
fig.show()


In [17]:
print (group['sensor_value'])

0        11734.0
49       11121.0
90       11138.0
131      11147.0
172      11119.0
          ...   
19500    10788.0
19541    10756.0
19582    10762.0
19623    10736.0
19664    10760.0
Name: sensor_value, Length: 473, dtype: float64


In [18]:
# Filter requirements.
order = 6
fs = 30.0  # sample rate, Hz
cutoff = 3.66  # desired cutoff frequency of the filter, Hz
window_size = 3
group_channel = 'sensor_value'
grouping_channel = ['experiment_id', 'heater_setting']

def apply_filter(group, order, fs, cutoff, target_channel, window_size):
    if target_channel not in group:
        raise KeyError(f"Column '{target_channel}' not found in the DataFrame")
    
    # print(f"Applying filter to group with target_channel: {target_channel}")
    
    # Get the filter coefficients
    b, a = butter(order, cutoff / (fs / 2), btype='low', analog=False)
    
    # # Apply the filter
    group['filtered'] = filtfilt(b, a, group[target_channel])
    
    # # Apply the rolling median
    group['filtered'] = group[target_channel].rolling(window_size, center=True).median()

     # Handle any remaining NaN values by filling them
    group['filtered'] = group['filtered'].fillna(method='bfill').fillna(method='ffill')
    
    return group

try:
    df_filtered = df.groupby(grouping_channel).apply(apply_filter, order=order, fs=fs, cutoff=cutoff, target_channel=group_channel, window_size=window_size).reset_index(drop=True)
    print(df_filtered.head())
except KeyError as e:
    print(e)

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\76768609.py:25: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\76768609.py:25: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\76768609.py:25: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\76768609.py:25: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\76768609.py:25: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() inste

          experiment_id  heater_setting  timestamp  sensor_value  channel_id  \
0  20240726121620s1c0r0             140     138336       11734.0           0   
1  20240726121620s1c0r0             140     138415       11121.0           0   
2  20240726121620s1c0r0             140     138459       11138.0           0   
3  20240726121620s1c0r0             140     138503       11147.0           0   
4  20240726121620s1c0r0             140     138546       11119.0           0   

   filtered  
0   11138.0  
1   11138.0  
2   11138.0  
3   11138.0  
4   11119.0  


In [19]:
filtered_grouped = df_filtered.groupby(grouping_channel, as_index=False, group_keys=False)
groups_filtered = list(filtered_grouped.groups.keys())
# Use the index to get the specific group
index = 0  # Replace with the desired index
experiment_id_value, heater_setting_value = groups_filtered[index]

# Fetch the specific group
f_group = filtered_grouped.get_group((experiment_id_value, heater_setting_value))

# Now you can plot this group
fig = px.line(f_group, x='timestamp', y='filtered', title=f'Experiment {experiment_id_value} - Heater Setting {heater_setting_value}')
fig.show()

In [20]:
# use the filtered column get the resistance
# convert to resistance where R_laod is R2 = 10kOhm input_voltage = 3.3V and 1_bit = 0.125mV (3.3V/2^14)

input_voltage = 3.3
RL_2 = 10000 # 10kOhm
adc_bit = 0.000125 # voltage of 1 bit in ADS1115
channel_to_convert = 'filtered'

# convert to resistance where R_laod is R2 = 10kOhm input_voltage = 3.3V and 1_bit = 0.125mV (3.3V/2^14)
df_normalized['Vo'] = df_filtered['sensor_value']*0.000125
df_normalized['resistance'] = (RL_2/df_normalized['Vo'])*((input_voltage/df_normalized['Vo'])-1)

def Vo2Resistance(group, target_channel, input_voltage, RL_2, bit_V, ):
    group['Vo'] = group[target_channel]*bit_V
    group['resistance'] = (RL_2/group['Vo'])*((input_voltage/group['Vo'])-1)
    return group

df_res = df_filtered.groupby(grouping_channel).apply(Vo2Resistance, target_channel=channel_to_convert, input_voltage=input_voltage, RL_2=RL_2, bit_V=adc_bit)
df_res = df_res.reset_index(drop=True)


C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\851410587.py:18: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



In [21]:
df_res.head()

experiment_id  heater_setting  timestamp  sensor_value  channel_id  \
0  20240726121620s1c0r0             140     138336       11734.0           0   
1  20240726121620s1c0r0             140     138415       11121.0           0   
2  20240726121620s1c0r0             140     138459       11138.0           0   
3  20240726121620s1c0r0             140     138503       11147.0           0   
4  20240726121620s1c0r0             140     138546       11119.0           0   

   filtered        Vo   resistance  
0   11138.0  1.392250  9842.082681  
1   11138.0  1.392250  9842.082681  
2   11138.0  1.392250  9842.082681  
3   11138.0  1.392250  9842.082681  
4   11119.0  1.389875  9888.041996

In [34]:
# def ratioCalculation(group):
#     # take the first 50 samples of the data as median to be the baseline
#     group['baseline'] = group['resistance'].head(50).median()
#     group['max_reaction_R'] = group['resistance'].min()
#     group['responsivity'] = (group['baseline']/group['max_reaction_R'])-1
#     return group

def ratioCalculation(group):
    # Calculate the baseline, max reaction resistance, and responsivity
    baseline_col = f"{group['heater_setting'].iloc[0]}_baseline"
    max_reaction_R_col = f"{group['heater_setting'].iloc[0]}_max_reaction_R"
    responsivity_col = f"{group['heater_setting'].iloc[0]}_responsivity"
    
    group[baseline_col] = group['resistance'].head(50).median()
    lowest_20_median = group['resistance'].nsmallest(20).median()
    group[max_reaction_R_col] = lowest_20_median
    # group[max_reaction_R_col] = group['resistance'].min()
    group[responsivity_col] = (group[baseline_col] / group[max_reaction_R_col]) - 1
    
    return group

df_full_feature = df_res.groupby(grouping_channel).apply(ratioCalculation)
df_full_feature = df_full_feature.reset_index(drop=True)
df_full_feature.head()

C:\Users\gavin\AppData\Local\Temp\ipykernel_13248\3855224999.py:22: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



experiment_id  heater_setting  timestamp  sensor_value  channel_id  \
0  20240726121620s1c0r0             140     138336       11734.0           0   
1  20240726121620s1c0r0             140     138415       11121.0           0   
2  20240726121620s1c0r0             140     138459       11138.0           0   
3  20240726121620s1c0r0             140     138503       11147.0           0   
4  20240726121620s1c0r0             140     138546       11119.0           0   

   filtered        Vo   resistance  140_baseline  140_max_reaction_R  ...  \
0   11138.0  1.392250  9842.082681   9813.187476         8603.167324  ...   
1   11138.0  1.392250  9842.082681   9813.187476         8603.167324  ...   
2   11138.0  1.392250  9842.082681   9813.187476         8603.167324  ...   
3   11138.0  1.392250  9842.082681   9813.187476         8603.167324  ...   
4   11119.0  1.389875  9888.041996   9813.187476         8603.167324  ...   

   242_responsivity  245_baseline  245_max_reaction_R  245_responsivity  \
0               NaN           NaN                 NaN               NaN   
1               NaN           NaN                 NaN               NaN   
2               NaN           NaN                 NaN               NaN   
3               NaN           NaN                 NaN               NaN   
4               NaN           NaN                 NaN               NaN   

   247_baseline  247_max_reaction_R  247_responsivity  250_baseline  \
0           NaN                 NaN               NaN           NaN   
1           NaN                 NaN               NaN           NaN   
2           NaN                 NaN               NaN           NaN   
3           NaN                 NaN               NaN           NaN   
4           NaN                 NaN               NaN           NaN   

   250_max_reaction_R  250_responsivity  
0                 NaN               NaN  
1                 NaN               NaN  
2                 NaN               NaN  
3                 NaN               NaN  
4                 NaN               NaN  

[5 rows x 131 columns]

In [35]:
# Extract relevant columns
metric_cols = [col for col in df_full_feature.columns if any(metric in col for metric in ['_baseline', '_max_reaction_R', '_responsivity'])]
df_metrics = df_full_feature[['experiment_id','channel_id'] + metric_cols].drop_duplicates()
# Melt the DataFrame to long format
df_melted = df_metrics.melt(id_vars=['experiment_id','channel_id'], value_vars=metric_cols, var_name='metric', value_name='value')

# Extract heater_setting and metric from the column names
df_melted[['heater_setting', 'metric']] = df_melted['metric'].str.extract(r'(\d+)_(baseline|max_reaction_R|responsivity)')
df_melted['heater_setting'] = df_melted['heater_setting'].astype(int)

# Pivot the DataFrame for each metric
df_pivoted = df_melted.pivot_table(index=['experiment_id','channel_id'], columns=['metric', 'heater_setting'], values='value')

# Flatten the MultiIndex columns
df_pivoted.columns = [f'{metric}_{heater_setting}' for metric, heater_setting in df_pivoted.columns]
df_pivoted = df_pivoted.reset_index()

In [37]:
df_pivoted.head()
df_pivoted.to_csv('3_features.csv', index=False)

In [27]:
# OLD pivot
# keep unique responsivity values after grouping
df_responsivity = df_full_feature.groupby(grouping_channel, as_index=False).first()
df_responsivity.head()

experiment_id  heater_setting  timestamp  sensor_value  channel_id  \
0  20240726121620s1c0r0             140     138336       11734.0           0   
1  20240726121620s1c0r0             150     138336       11734.0           0   
2  20240726121620s1c0r0             152     138337       11734.0           0   
3  20240726121620s1c0r0             155     138337       11734.0           0   
4  20240726121620s1c0r0             157     138337       11734.0           0   

   filtered        Vo    resistance  140_baseline  140_max_reaction_R  ...  \
0   11138.0  1.392250   9842.082681   9813.187476         8603.167324  ...   
1   11147.0  1.393375   9820.401749           NaN                 NaN  ...   
2   10855.0  1.356875  10554.096427           NaN                 NaN  ...   
3   10453.0  1.306625  11675.811648           NaN                 NaN  ...   
4   10453.0  1.306625  11675.811648           NaN                 NaN  ...   

   242_responsivity  245_baseline  245_max_reaction_R  245_responsivity  \
0               NaN           NaN                 NaN               NaN   
1               NaN           NaN                 NaN               NaN   
2               NaN           NaN                 NaN               NaN   
3               NaN           NaN                 NaN               NaN   
4               NaN           NaN                 NaN               NaN   

   247_baseline  247_max_reaction_R  247_responsivity  250_baseline  \
0           NaN                 NaN               NaN           NaN   
1           NaN                 NaN               NaN           NaN   
2           NaN                 NaN               NaN           NaN   
3           NaN                 NaN               NaN           NaN   
4           NaN                 NaN               NaN           NaN   

   250_max_reaction_R  250_responsivity  
0                 NaN               NaN  
1                 NaN               NaN  
2                 NaN               NaN  
3                 NaN               NaN  
4                 NaN               NaN  

[5 rows x 131 columns]

In [25]:
# plot the responsivity against the heater setting within each experiment_id
fig = px.line(df_responsivity, x='heater_setting', y='responsivity', color='experiment_id', title='Responsivity vs. Heater Setting')
fig.show()

ValueError: Value of 'y' is not the name of a column in 'data_frame'. Expected one of ['experiment_id', 'heater_setting', 'timestamp', 'sensor_value', 'channel_id', 'filtered', 'Vo', 'resistance', '140_baseline', '140_max_reaction_R', '140_responsivity', '150_baseline', '150_max_reaction_R', '150_responsivity', '152_baseline', '152_max_reaction_R', '152_responsivity', '155_baseline', '155_max_reaction_R', '155_responsivity', '157_baseline', '157_max_reaction_R', '157_responsivity', '160_baseline', '160_max_reaction_R', '160_responsivity', '162_baseline', '162_max_reaction_R', '162_responsivity', '165_baseline', '165_max_reaction_R', '165_responsivity', '167_baseline', '167_max_reaction_R', '167_responsivity', '170_baseline', '170_max_reaction_R', '170_responsivity', '172_baseline', '172_max_reaction_R', '172_responsivity', '175_baseline', '175_max_reaction_R', '175_responsivity', '177_baseline', '177_max_reaction_R', '177_responsivity', '180_baseline', '180_max_reaction_R', '180_respon

In [16]:
# transpose the responsivity values to have heater setting as columns and experiment_id as index
df_responsivity_pivot = df_responsivity.pivot(index='experiment_id', columns='heater_setting', values='responsivity')
df_responsivity_pivot.head()

heater_setting             140       150       152       155       157  \
experiment_id                                                            
20240726121620s1c0r0  0.148303  0.107819  0.065073  0.104760  0.100230   
20240726121655s1c1r0  0.034741  0.108235  0.163589  0.347983  0.410756   
20240726121731s1c2r0  0.043338  0.087611  0.170897  0.426941  0.546122   
20240726121807s1c3r0  0.075550  0.130130  0.157919  0.355258  0.444765   
20240726121842s1c4r0  2.051198  2.081876  2.237846  2.557322  2.445346   

heater_setting             160       162       165       167       170  ...  \
experiment_id                                                           ...   
20240726121620s1c0r0  0.133083  0.135211  0.110151  0.107327  0.089585  ...   
20240726121655s1c1r0  0.480319  0.451880  0.462353  0.403136  0.379845  ...   
20240726121731s1c2r0  0.578038  0.549649  0.484011  0.456133  0.411122  ...   
20240726121807s1c3r0  0.500961  0.520981  0.472456  0.438508  0.408007  ...   
20240726121842s1c4r0  2.584304  2.485132  2.451731  2.306597  2.186628  ...   

heater_setting             227       230       232       235       237  \
experiment_id                                                            
20240726121620s1c0r0  0.219854  0.223158  0.221262  0.208559  0.198966   
20240726121655s1c1r0  0.035271  0.043439  0.046742  0.049208  0.041590   
20240726121731s1c2r0  0.054123  0.056763  0.052382  0.042189  0.044251   
20240726121807s1c3r0  0.097581  0.077386  0.085839  0.087621  0.081636   
20240726121842s1c4r0  2.142425  2.156540  2.199868  2.183455  2.158737   

heater_setting             240       242       245       247       250  
experiment_id                                                           
20240726121620s1c0r0  0.199478  0.186100  0.182118  0.173960  0.160026  
20240726121655s1c1r0  0.042110  0.038038  0.037400  0.035662  0.036163  
20240726121731s1c2r0  0.053702  0.046208  0.049809  0.048673  0.045162  
20240726121807s1c3r0  0.089030  0.087135  0.083566  0.082772  0.077094  
20240726121842s1c4r0  2.167883  2.134211  2.115313  2.115739  2.110130  

[5 rows x 41 columns]

In [17]:
# append channel_id according to experiment_id to the last column of the responsivity pivot table
df_responsivity_pivot['channel_id'] = df_responsivity_pivot.index.map(lambda x: df_responsivity[df_responsivity['experiment_id'] == x]['channel_id'].values[0])
df_responsivity_pivot.head(10)

heater_setting             140       150       152       155       157  \
experiment_id                                                            
20240726121620s1c0r0  0.148303  0.107819  0.065073  0.104760  0.100230   
20240726121655s1c1r0  0.034741  0.108235  0.163589  0.347983  0.410756   
20240726121731s1c2r0  0.043338  0.087611  0.170897  0.426941  0.546122   
20240726121807s1c3r0  0.075550  0.130130  0.157919  0.355258  0.444765   
20240726121842s1c4r0  2.051198  2.081876  2.237846  2.557322  2.445346   
20240726121918s1c0r1  0.063411  0.160246  0.242078  0.372482  0.536965   
20240726121953s1c1r1  0.064071  0.143017  0.301186  0.685702  0.756423   
20240726122029s1c2r1  0.043228  0.101172  0.293011  0.362158  0.516703   
20240726122104s1c3r1  0.056943  0.162828  0.404236  0.656925  0.722863   
20240726122140s1c4r1  2.284645  2.291245  1.914847  2.037808  2.237182   

heater_setting             160       162       165       167       170  ...  \
experiment_id                                                           ...   
20240726121620s1c0r0  0.133083  0.135211  0.110151  0.107327  0.089585  ...   
20240726121655s1c1r0  0.480319  0.451880  0.462353  0.403136  0.379845  ...   
20240726121731s1c2r0  0.578038  0.549649  0.484011  0.456133  0.411122  ...   
20240726121807s1c3r0  0.500961  0.520981  0.472456  0.438508  0.408007  ...   
20240726121842s1c4r0  2.584304  2.485132  2.451731  2.306597  2.186628  ...   
20240726121918s1c0r1  0.579678  0.543181  0.525653  0.464448  0.372089  ...   
20240726121953s1c1r1  0.575682  0.515178  0.571761  0.538594  0.468950  ...   
20240726122029s1c2r1  0.672261  0.577666  0.527281  0.484822  0.425188  ...   
20240726122104s1c3r1  0.706489  0.661104  0.547045  0.542190  0.390619  ...   
20240726122140s1c4r1  2.184714  2.264301  2.062911  1.956535  1.758155  ...   

heater_setting             230       232       235       237       240  \
experiment_id                                                            
20240726121620s1c0r0  0.223158  0.221262  0.208559  0.198966  0.199478   
20240726121655s1c1r0  0.043439  0.046742  0.049208  0.041590  0.042110   
20240726121731s1c2r0  0.056763  0.052382  0.042189  0.044251  0.053702   
20240726121807s1c3r0  0.077386  0.085839  0.087621  0.081636  0.089030   
20240726121842s1c4r0  2.156540  2.199868  2.183455  2.158737  2.167883   
20240726121918s1c0r1  0.083355  0.075012  0.076634  0.070976  0.079557   
20240726121953s1c1r1  0.081404  0.091355  0.086794  0.088200  0.085035   
20240726122029s1c2r1  0.059748  0.047360  0.048563  0.053577  0.059261   
20240726122104s1c3r1  0.076113  0.079026  0.076259  0.089480  0.084160   
20240726122140s1c4r1  2.429471  2.428782  2.404992  2.421965  2.381391   

heater_setting             242       245       247       250  channel_id  
experiment_id                                                             
20240726121620s1c0r0  0.186100  0.182118  0.173960  0.160026           0  
20240726121655s1c1r0  0.038038  0.037400  0.035662  0.036163           1  
20240726121731s1c2r0  0.046208  0.049809  0.048673  0.045162           2  
20240726121807s1c3r0  0.087135  0.083566  0.082772  0.077094           3  
20240726121842s1c4r0  2.134211  2.115313  2.115739  2.110130           4  
20240726121918s1c0r1  0.079406  0.063805  0.067022  0.069219           0  
20240726121953s1c1r1  0.080311  0.074096  0.079921  0.066469           1  
20240726122029s1c2r1  0.053438  0.041620  0.043968  0.049145           2  
20240726122104s1c3r1  0.068160  0.061140  0.065903  0.069961           3  
20240726122140s1c4r1  2.382677  2.336610  2.358819  2.337792           4  

[10 rows x 42 columns]

In [18]:
# save df_responsivity_pivot to a csv file
df_responsivity_pivot.to_csv('feature_matrix_2.csv')